# IBM FINAL CAPSTONE PROJECT - The Battle of the Neighborhoods

In [13]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#import folium # map rendering library

print("Libraries imported.")


Libraries imported.


In [14]:
data = requests.get('https://familypedia.wikia.org/wiki/List_of_incorporated_cities_and_towns_in_California').text

In [15]:
soup = BeautifulSoup(data, 'html.parser')
#soup

In [16]:

boroughList = []
neighborhoodList = []

In [17]:
for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        neighborhoodList.append(cells[0].text.rstrip('\n'))
        boroughList.append(cells[1].text.rstrip('\n'))
        

In [18]:
# create a new DataFrame from the three lists
df = pd.DataFrame({"Neighborhood": neighborhoodList,
                           "Borough": boroughList})

df.head()

Neighborhood           Borough
0       Adelanto    San Bernardino 
1   Agoura Hills       Los Angeles 
2        Alameda           Alameda 
3         Albany           Alameda 
4       Alhambra       Los Angeles

In [19]:
print('The dataframe has {} boroughs and {} df.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 57 boroughs and 481 df.


In [20]:
!pip install geocoder

In [21]:
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder

In [22]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Los Angeles, California'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [23]:
coords = [ get_latlng(neighborhood) for neighborhood in df["Neighborhood"].tolist() ]
coords[:5]

[[34.123802931115975, -118.1714225160321],
 [34.14611000000008, -118.77811999999994],
 [33.96998612085879, -118.23379665086239],
 [34.0448148653588, -118.27312453087512],
 [34.09370000000007, -118.12726999999995]]

In [24]:
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [25]:
df['Latitude'] = df_coords['Latitude']
df['Longitude'] = df_coords['Longitude']

In [26]:
df.head()

Neighborhood           Borough   Latitude   Longitude
0       Adelanto    San Bernardino   34.123803 -118.171423
1   Agoura Hills       Los Angeles   34.146110 -118.778120
2        Alameda           Alameda   33.969986 -118.233797
3         Albany           Alameda   34.044815 -118.273125
4       Alhambra       Los Angeles   34.093700 -118.127270

In [28]:
dff=df.sort_values(by=['Borough']).reset_index(drop=True)
dff.head()

Neighborhood    Borough   Latitude   Longitude
0      Berkeley    Alameda   34.087400 -118.269505
1    Emeryville    Alameda   34.168300 -118.610220
2   San Leandro    Alameda   34.394124 -118.474170
3      Piedmont    Alameda   34.113107 -118.189395
4     Oakland †    Alameda   34.088916 -118.165792

In [30]:
dff = dff[['Borough','Neighborhood','Latitude','Longitude']]
dff.head()

Borough   Neighborhood   Latitude   Longitude
0   Alameda       Berkeley   34.087400 -118.269505
1   Alameda     Emeryville   34.168300 -118.610220
2   Alameda    San Leandro   34.394124 -118.474170
3   Alameda       Piedmont   34.113107 -118.189395
4   Alameda      Oakland †   34.088916 -118.165792

In [18]:
#dff[dff.Borough == 'Alameda']
#rainfall_df[rainfall_df.ward_id != 36]

#df.loc[df['column_name'] == some_value]

In [31]:
dff=dff.loc[99:186]
dff

Borough             Neighborhood  Latitude  Longitude
99    Los Angeles            Hermosa Beach   33.86404 -118.39535
100   Los Angeles                  Gardena   33.88379 -118.30702
101   Los Angeles                 Glendale   34.14633 -118.24864
102   Los Angeles              Signal Hill   33.79677 -118.16770
103   Los Angeles                 Industry   34.02336 -117.95661
104   Los Angeles                 Glendora   34.13602 -117.86452
105   Los Angeles          Huntington Park   33.98143 -118.21914
106   Los Angeles         Hawaiian Gardens   33.83082 -118.08184
107   Los Angeles             Sierra Madre   34.16187 -118.05716
108   Los Angeles                Inglewood   33.96178 -118.35653
109   Los Angeles             Hidden Hills   34.15918 -118.64025
110   Los Angeles                Hawthorne   33.91822 -118.35273
111   Los Angeles     La Cañada Flintridge   34.20766 -118.20725
112   Los Angeles            Monterey Park   34.05979 -118.12651
113   Los Angeles              San Gabriel   34.09723 -118.10842
114   Los Angeles             San Fernando   34.28406 -118.43844
115   Los Angeles                  Norwalk   33.91681 -118.07252
116   Los Angeles                San Dimas   34.10668 -117.80298
117   Los Angeles                 Palmdale   34.57936 -118.11659
118   Los Angeles     Palos Verdes Estates   33.80003 -118.39187
119   Los Angeles                Paramount   33.88516 -118.16140
120   Los Angeles                 Pasadena   34.14745 -118.14427
121   Los Angeles                 Rosemead   34.08075 -118.07562
122   Los Angeles              Pico Rivera   33.98242 -118.08799
123   Los Angeles    Rolling Hills Estates   33.78359 -118.35377
124   Los Angeles                   Pomona   34.05499 -117.75004
125   Los Angeles            Rolling Hills   33.77609 -118.34399
126   Los Angeles      Rancho Palos Verdes   33.74526 -118.40378
127   Los Angeles               Montebello   34.01959 -118.11643
128   Los Angeles                Irwindale   34.10514 -117.93377
129   Los Angeles                 Monrovia   34.14783 -117.99878
130   Los Angeles                  Maywood   33.98757 -118.18981
131   Los Angeles         La Habra Heights   33.94813 -117.96483
132   Los Angeles             Santa Monica   34.01158 -118.49227
133   Los Angeles                La Mirada   33.90853 -118.01173
134   Los Angeles                La Puente   34.02012 -117.95040
135   Los Angeles                 La Verne   34.11300 -117.76528
136   Los Angeles                 Lakewood   33.85001 -118.13384
137   Los Angeles                Lancaster   34.69890 -118.14478
138   Los Angeles                 Lawndale   33.89862 -118.35385
139   Los Angeles         Santa Fe Springs   33.94649 -118.08384
140   Los Angeles            Santa Clarita   34.41387 -118.55121
141   Los Angeles                   Lomita   33.80528 -118.31990
142   Los Angeles               Long Beach   33.76672 -118.19240
143   Los Angeles            Los Angeles †   34.05361 -118.24550
144   Los Angeles                  Lynwood   33.92783 -118.19927
145   Los Angeles          Manhattan Beach   33.88720 -118.41086
146   Los Angeles               San Marino   34.12208 -118.10521
147   Los Angeles                   Malibu   34.03652 -118.68796
148   Los Angeles            Redondo Beach   33.84445 -118.38794
149   Los Angeles               Bellflower   33.88326 -118.12229
150   Los Angeles               El Segundo   33.92084 -118.41597
151   Los Angeles                 El Monte   34.07105 -118.03094
152   Los Angeles                   Cudahy   33.95987 -118.17637
153   Los Angeles              Culver City   34.02161 -118.39621
154   Los Angeles                 Whittier   33.97542 -118.03386
155   Los Angeles                 Cerritos   33.86866 -118.06370
156   Los Angeles                   Duarte   34.13961 -117.97050
157   Los Angeles            Beverly Hills   34.07346 -118.40032
158   Los Angeles                   Carson   33.83161 -118.26209
159   Los Angeles                 Bradbury   3

In [20]:
address = 'Los Angeles'

geolocator = Nominatim(user_agent="cal_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 34.0536909, -118.2427666.


In [21]:
# create map of Manhattan using latitude and longitude values
!pip install folium
import folium


     |████████████████████████████████| 102kB 2.1MB/s ta 0:00:01


In [22]:
map_los = folium.Map(location=[latitude, longitude], zoom_start=8)

# add markers to map
for lat, lng, label in zip(dff['Latitude'], dff['Longitude'], dff['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_los)  
    
map_los

In [1]:
CLIENT_ID =   'your Foursquare ID'
CLIENT_SECRET =   'your Foursquare Secret'
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: your Foursquare ID
CLIENT_SECRET:your Foursquare Secret


In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    LIMIT=100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [25]:
#Get venues for all neighborhoods in our dataset
Los_venues = getNearbyVenues(names=dff['Neighborhood'],
                                latitudes=dff['Latitude'],
                                longitudes=dff['Longitude'])

 Belvedere 
 Tiburon * 
 Point Arena 
 Fort Bragg 
 Willits 
 Ukiah † 
 Gustine 
 Los Banos 
 Atwater 
 Livingston 
 Merced † 
 Dos Palos 
 Alturas † 
 Mammoth Lakes * 
 Pacific Grove 
 Sand City 
 Marina 
 Carmel-by-the-Sea 
 Salinas † 
 Monterey 
 Soledad 
 Gonzales 
 Greenfield 
 King City 
 Del Rey Oaks 
 Seaside 
 Yountville * 
 St. Helena 
 Calistoga 
 American Canyon 
 Napa † 
 Truckee * 
 Grass Valley 
 Nevada City † 
 Cypress 
 Huntington Beach 
 Buena Park 
 Dana Point 
 Brea 
 Westminster 
 Mission Viejo 
 Stanton 
 La Habra 
 San Clemente 
 San Juan Capistrano 
 Orange 
 Seal Beach 
 Lake Forest 
 Tustin 
 Newport Beach 
 La Palma 
 Anaheim 
 Laguna Niguel 
 Aliso Viejo 
 Laguna Woods 
 Los Alamitos 
 Laguna Hills 
 Laguna Beach 
 Garden Grove 
 Rancho Santa Margarita 
 Costa Mesa 
 Santa Ana † 
 Yorba Linda 
 Villa Park 
 Placentia 
 Fountain Valley 
 Fullerton 
 Irvine 
 Lincoln 
 Colfax 
 Auburn † 
 Rocklin 
 Loomis * 
 Roseville 
 Portola 
 Palm Desert 
 Hemet 
 Eastval

In [27]:
Los_venues.shape

(2503, 7)

In [28]:
Los_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Belvedere                 34.0406              -118.16751   
1   Belvedere                 34.0406              -118.16751   
2   Belvedere                 34.0406              -118.16751   
3   Belvedere                 34.0406              -118.16751   
4   Belvedere                 34.0406              -118.16751   

                   Venue  Venue Latitude  Venue Longitude  \
0  La Azteca Tortilleria       34.040503      -118.168017   
1        El Gallo Bakery       34.040508      -118.167820   
2           Moles La Tia       34.040730      -118.166483   
3      Cities Restaurant       34.040397      -118.168837   
4       Tamales Lilianas       34.040976      -118.165810   

              Venue Category  
0  Latin American Restaurant  
1                     Bakery  
2         Mexican Restaurant  
3                     Lounge  
4         Mexican Restaurant

In [29]:
Los_venues['Venue Category'].value_counts()

Mexican Restaurant                          116
Coffee Shop                                 101
Pizza Place                                  75
Park                                         48
Café                                         47
Sandwich Place                               46
American Restaurant                          45
Fast Food Restaurant                         42
Chinese Restaurant                           42
Restaurant                                   40
Bakery                                       39
Thai Restaurant                              37
Convenience Store                            36
Food Truck                                   32
Hotel                                        31
Grocery Store                                31
Bar                                          31
Trail                                        30
Clothing Store                               29
Italian Restaurant                           29
Ice Cream Shop                          

In [30]:
Los_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                              
 Adelanto                                     5                       5   
 Aliso Viejo                                 13                      13   
 Alturas †                                    4                       4   
 American Canyon                              2                       2   
 Anaheim                                      1                       1   
 Apple Valley *                              13                      13   
 Atwater                                     36                      36   
 Auburn †                                    14                      14   
 Banning                                     31                      31   
 Barstow                                     15                      15   
 Beaumont                                     4                       4   
 Belvedere                                   20                      20   
 Big Bear Lake                                4                       4   
 Blythe                                      27                      27   
 Brea                                        29                      29   
 Buellton                                    34                      34   
 Buena Park                                  18                      18   
 Calimesa                                    34                      34   
 Calistoga                                    1                       1   
 Campbell                                    31                      31   
 Canyon Lake                                  1                       1   
 Capitola                                     2                       2   
 Carlsbad                                     7                       7   
 Carmel-by-the-Sea                           92                      92   
 Carpinteria                                 13                      13   
 Cathedral City                               2                       2   
 Chino                                        1                       1   
 Chula Vista                                 25                      25   
 Citrus Heights                               1                       1   
 Coachella                                    5                       5   
 Colfax                                      19                      19   
 Colton                                      23                      23   
 Corona                                       7                       7   
 Coronado                                    26                      26   
 Costa Mesa                                   3                       3   
 Cupertino                                   34                      34   
 Cypress                                     28                      28   
 Dana Point                                  17                      17   
 Del Mar                                     43                      43   
 Del Rey Oaks                                24                      24   
 Desert Hot Springs                           6                       6   
 Dos Palos                                   12                      12   
 El Cajon                                     2                       2   
 Elk Grove                                    4                       4   
 Folsom                                       5                       5   
 Fontana                                      8                       8   
 Fort Bragg                                  34                      34   
 Fountain Valley                             17                      17   
 Fullerton                                   53                      53   
 Galt                                         6                       6   
 Garden Grove                                14                      14   
 Gilroy                                      23    

In [31]:

#Number of unique venue categories
print('There are {} uniques categories.'.format(len(Los_venues['Venue Category'].unique())))

There are 278 uniques categories.


In [32]:
Los_venues['Venue Category'].unique()[:100]

array(['Latin American Restaurant', 'Bakery', 'Mexican Restaurant',
       'Lounge', 'Juice Bar', 'Sandwich Place', 'Pizza Place',
       'Breakfast Spot', 'Café', 'Restaurant', 'Taco Place',
       'Gas Station', 'Martial Arts School', 'Food Truck', 'Donut Shop',
       'Tea Room', 'Plaza', 'Korean Restaurant', 'Thai Restaurant',
       'Chinese Restaurant', 'Noodle House', 'Bubble Tea Shop',
       'Hobby Shop', 'Miscellaneous Shop', 'Arcade', 'Asian Restaurant',
       'Music Store', 'Sushi Restaurant', 'Electronics Store', 'ATM',
       'Liquor Store', 'Park', 'Speakeasy', 'Smoke Shop',
       'Indian Restaurant', 'American Restaurant', 'Coffee Shop',
       'Building', 'Concert Hall', 'School', 'Art Museum', 'Market',
       'Performing Arts Venue', 'Cheese Shop', 'Ice Cream Shop',
       'Filipino Restaurant', 'Music Venue', 'Deli / Bodega',
       'General Entertainment', 'Bookstore', 'Opera House',
       'Seafood Restaurant', 'Train Station', 'Burger Joint',
       'Fast Food 

In [33]:

'Indian Restaurant' in Los_venues['Venue Category'].unique()

True

In [34]:
to_onehot = pd.get_dummies(Los_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = Los_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(2503, 279)


Neighborhoods  ATM  Accessories Store  Adult Boutique  American Restaurant  \
0    Belvedere     0                  0               0                    0   
1    Belvedere     0                  0               0                    0   
2    Belvedere     0                  0               0                    0   
3    Belvedere     0                  0               0                    0   
4    Belvedere     0                  0               0                    0   

   Antique Shop  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0       0            0           0                    0   
1             0       0            0           0                    0   
2             0       0            0           0                    0   
3             0       0            0           0                    0   
4             0       0            0           0                    0   

   Asian Restaurant  Assisted Living  Astrologer  Athletics & Sports  \
0                 0                0           0                   0   
1                 0                0           0                   0   
2                 0                0           0                   0   
3                 0                0           0                   0   
4                 0                0           0                   0   

   Australian Restaurant  Auto Garage  Automotive Shop  BBQ Joint  Bagel Shop  \
0                      0            0                0          0           0   
1                      0            0                0          0           0   
2                      0            0                0          0           0   
3                      0            0                0          0           0   
4                      0            0                0          0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       1     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Beach  Bed & Breakfast  Beer Garden  Beer Store  Big Box Store  Bistro  \
0      0                0            0           0              0       0   
1      0                0            0           0              0       0   
2      0                0            0           0              0       0   
3      0                0            0           0              0       0   
4      0                0            0           0              0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  Boxing Gym  \
0           0              0          0         0              0           0   
1           0              0          0         0              0           0   
2           0              0          0         0              0           0   
3           0              0          0         0              0           0   
4           0              0          0         0              0           0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0               0        0            0       0   

   Bubble Tea Shop  Building  Burger Joint  Burmese Restaurant  Burrito Place  \
0                0         0             0                   0              0   
1                0         0             0                   0              0   
2                0         0             0                   0              0  

In [35]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(162, 279)


Neighborhoods       ATM  Accessories Store  Adult Boutique  \
0                   Adelanto   0.000000           0.000000        0.000000   
1                Aliso Viejo   0.000000           0.000000        0.000000   
2                  Alturas †   0.000000           0.000000        0.000000   
3            American Canyon   0.000000           0.000000        0.000000   
4                    Anaheim   0.000000           0.000000        0.000000   
5             Apple Valley *   0.000000           0.000000        0.000000   
6                    Atwater   0.000000           0.000000        0.000000   
7                   Auburn †   0.000000           0.000000        0.000000   
8                    Banning   0.000000           0.000000        0.000000   
9                    Barstow   0.000000           0.000000        0.000000   
10                  Beaumont   0.000000           0.000000        0.000000   
11                 Belvedere   0.000000           0.000000        0.000000   
12             Big Bear Lake   0.000000           0.000000        0.000000   
13                    Blythe   0.037037           0.000000        0.000000   
14                      Brea   0.000000           0.034483        0.000000   
15                  Buellton   0.000000           0.000000        0.000000   
16                Buena Park   0.000000           0.000000        0.000000   
17                  Calimesa   0.000000           0.000000        0.000000   
18                 Calistoga   0.000000           0.000000        0.000000   
19                  Campbell   0.000000           0.000000        0.000000   
20               Canyon Lake   0.000000           0.000000        0.000000   
21                  Capitola   0.000000           0.000000        0.000000   
22                  Carlsbad   0.000000           0.000000        0.000000   
23         Carmel-by-the-Sea   0.000000           0.000000        0.000000   
24               Carpinteria   0.000000           0.076923        0.000000   
25            Cathedral City   0.000000           0.000000        0.000000   
26                     Chino   0.000000           0.000000        0.000000   
27               Chula Vista   0.000000           0.000000        0.000000   
28            Citrus Heights   0.000000           0.000000        0.000000   
29                 Coachella   0.000000           0.000000        0.000000   
30                    Colfax   0.000000           0.000000        0.000000   
31                    Colton   0.000000           0.000000        0.000000   
32                    Corona   0.000000           0.142857        0.000000   
33                  Coronado   0.000000           0.000000        0.000000   
34                Costa Mesa   0.000000           0.000000        0.000000   
35                 Cupertino   0.000000           0.000000        0.000000   
36                   Cypress   0.000000           0.000000        0.000000   
37                Dana Point   0.058824           0.000000        0.000000   
38                   Del Mar   0.000000           0.000000        0.023256   
39              Del Rey Oaks   0.000000           0.000000        0.000000   
40        Desert Hot Springs   0.000000           0.000000        0.000000   
41                 Dos Palos   0.000000           0.000000        0.000000   
42                  El Cajon   0.000000           0.000000        0.000000   
43                 Elk Grove   0.000000           0.000000        0.000000   
44                    Folsom   0.000000           0.000000        0.000000   
45                   Fontana   0.000000           0.000000        0.000000   
46                Fort Bragg   0.000000           0.000000        0.000000   
47           Fountain Valley   0.000000           0.000000        0.000000   
48                 Fullerton   0.000000           0.000000        0.000000   
49                      Galt   0.000000           0.000000        0.000000   
50              Garden Grove   0.00000

In [36]:
len(to_grouped[to_grouped["Indian Restaurant"] > 0])

17

In [37]:
to_indian = to_grouped[["Neighborhoods","Indian Restaurant"]]

In [38]:
to_indian

Neighborhoods  Indian Restaurant
0                   Adelanto            0.000000
1                Aliso Viejo            0.000000
2                  Alturas †            0.000000
3            American Canyon            0.000000
4                    Anaheim            0.000000
5             Apple Valley *            0.000000
6                    Atwater            0.000000
7                   Auburn †            0.000000
8                    Banning            0.000000
9                    Barstow            0.000000
10                  Beaumont            0.000000
11                 Belvedere            0.000000
12             Big Bear Lake            0.000000
13                    Blythe            0.000000
14                      Brea            0.000000
15                  Buellton            0.029412
16                Buena Park            0.000000
17                  Calimesa            0.029412
18                 Calistoga            0.000000
19                  Campbell            0.000000
20               Canyon Lake            0.000000
21                  Capitola            0.000000
22                  Carlsbad            0.000000
23         Carmel-by-the-Sea            0.000000
24               Carpinteria            0.000000
25            Cathedral City            0.000000
26                     Chino            0.000000
27               Chula Vista            0.000000
28            Citrus Heights            0.000000
29                 Coachella            0.000000
30                    Colfax            0.000000
31                    Colton            0.000000
32                    Corona            0.000000
33                  Coronado            0.000000
34                Costa Mesa            0.000000
35                 Cupertino            0.029412
36                   Cypress            0.000000
37                Dana Point            0.058824
38                   Del Mar            0.000000
39              Del Rey Oaks            0.000000
40        Desert Hot Springs            0.000000
41                 Dos Palos            0.000000
42                  El Cajon            0.000000
43                 Elk Grove            0.000000
44                    Folsom            0.000000
45                   Fontana            0.000000
46                Fort Bragg            0.029412
47           Fountain Valley            0.000000
48                 Fullerton            0.000000
49                      Galt            0.000000
50              Garden Grove            0.000000
51                    Gilroy            0.000000
52                  Gonzales            0.000000
53             Grand Terrace            0.000000
54              Grass Valley            0.000000
55                Greenfield            0.017857
56                 Guadalupe            0.000000
57                   Gustine            0.000000
58                     Hemet            0.038462
59                  Hesperia            0.000000
60                  Highland            0.000000
61               Hollister †            0.000000
62          Huntington Beach            0.040000
63            Imperial Beach            0.000000
64              Indian Wells            0.000000
65                     Indio            0.000000
66                    Irvine            0.000000
67                   Isleton            0.029412
68                 King City            0.000000
69                  La Habra            0.000000
70                   La Mesa            0.000000
71                  La Palma            0.000000
72                 La Quinta            0.000000
73              Laguna Beach            0.000000
74              Laguna Hills            0.000000
75             Laguna Niguel            0.000000
76              Laguna Woods            0.000000
77             Lake Elsinore            0.000000
78               Lake Forest            0.000000
79               Lemon Grove            0.000000
80                   Lincoln            0.00000

In [39]:
from sklearn.cluster import KMeans
toclusters = 3

to_clustering = to_indian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=1)
kmeans.fit_transform(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1],
      dtype=int32)

In [40]:
to_merged = to_indian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [41]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head(5)

Neighborhood  Indian Restaurant  Cluster Labels
0          Adelanto                 0.0               1
1       Aliso Viejo                 0.0               1
2         Alturas †                 0.0               1
3   American Canyon                 0.0               1
4           Anaheim                 0.0               1

In [42]:
to_merged = to_merged.join(Los_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(2503, 9)


Neighborhood  Indian Restaurant  Cluster Labels  Neighborhood Latitude  \
0    Adelanto                 0.0               1              34.123803   
0    Adelanto                 0.0               1              34.123803   
0    Adelanto                 0.0               1              34.123803   
0    Adelanto                 0.0               1              34.123803   
0    Adelanto                 0.0               1              34.123803   

   Neighborhood Longitude                                              Venue  \
0             -118.171423  http://www.amazon.com/gp/aw/sitb/B0018A01L4/?r...   
0             -118.171423                         Jamie's Dance and BarBa Q.   
0             -118.171423                      Midtown Builders and Plumbers   
0             -118.171423                       Miracle Garage Doors Service   
0             -118.171423                                   San Pascual Park   

   Venue Latitude  Venue Longitude              Venue Category  
0       34.124012      -118.172566               Moving Target  
0       34.122489      -118.169918                   BBQ Joint  
0       34.125250      -118.168976  Construction & Landscaping  
0       34.125760      -118.169203                Home Service  
0       34.120342      -118.168870                        Park

In [43]:
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged.head()

Neighborhood  Indian Restaurant  Cluster Labels  Neighborhood Latitude  \
119    Redlands            0.055556               0              33.953853   
123   Roseville            0.062500               0              38.706468   
123   Roseville            0.062500               0              38.706468   
123   Roseville            0.062500               0              38.706468   
123   Roseville            0.062500               0              38.706468   

     Neighborhood Longitude                     Venue  Venue Latitude  \
119             -118.443205           Del Rey Deli Co       33.956099   
123             -121.327709                 Quik Stop       38.704866   
123             -121.327709      Pisor Fence Division       38.709990   
123             -121.327709  Walmart Vision & Glasses       38.704051   
123             -121.327709       Walmart Supercenter       38.704136   

     Venue Longitude Venue Category  
119      -118.442545  Deli / Bodega  
123      -121.327126    Gas Station  
123      -121.329052  Moving Target  
123      -121.331655   Optical Shop  
123      -121.331745  Big Box Store

In [44]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=9)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [45]:

# save the map as HTML file
map_clusters.save('map_clusters.html')

In [46]:
#Cluster 0
to_merged.loc[(to_merged['Cluster Labels'] ==0) & (to_merged['Venue Category'] == 'Indian Restaurant') ]

Neighborhood  Indian Restaurant  Cluster Labels  Neighborhood Latitude  \
119     Redlands            0.055556               0              33.953853   
123    Roseville            0.062500               0              38.706468   
142      Seaside            0.071429               0              33.825300   
37    Dana Point            0.058824               0              34.031585   

     Neighborhood Longitude                 Venue  Venue Latitude  \
119             -118.443205       Tandoor A India       33.957206   
123             -121.327709  Great Indian Cuisine       38.704801   
142             -118.369320              Red Fort       33.825100   
37              -118.292890  Manas Indian Cuisine       34.028826   

     Venue Longitude     Venue Category  
119      -118.442808  Indian Restaurant  
123      -121.326851  Indian Restaurant  
142      -118.369019  Indian Restaurant  
37       -118.291656  Indian Restaurant

In [47]:
#Cluster 1
to_merged.loc[(to_merged['Cluster Labels'] ==1) & (to_merged['Venue Category'] == 'Indian Restaurant') ]

Empty DataFrame
Columns: [Neighborhood, Indian Restaurant, Cluster Labels, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue Category]
Index: []

In [48]:
#Cluster 2
to_merged.loc[(to_merged['Cluster Labels'] ==2) & (to_merged['Venue Category'] == 'Indian Restaurant') ]

Neighborhood  Indian Restaurant  Cluster Labels  \
15            Buellton            0.029412               2   
160            Yucaipa            0.029412               2   
135    Santa Barbara †            0.027778               2   
17            Calimesa            0.029412               2   
55          Greenfield            0.017857               2   
62    Huntington Beach            0.040000               2   
58               Hemet            0.038462               2   
67             Isleton            0.029412               2   
46          Fort Bragg            0.029412               2   
122            Rocklin            0.029412               2   
35           Cupertino            0.029412               2   
89             Menifee            0.029412               2   
101      Nevada City †            0.029412               2   

     Neighborhood Latitude  Neighborhood Longitude  \
15               34.053610             -118.245500   
160              34.053610             -118.245500   
135              34.012639             -118.339951   
17               34.053610             -118.245500   
55               34.047145             -118.439985   
62               34.130765             -118.069415   
58               34.102097             -118.364673   
67               34.053610             -118.245500   
46               34.053610             -118.245500   
122              34.053610             -118.245500   
35               34.053610             -118.245500   
89               34.053610             -118.245500   
101              34.053610             -118.245500   

                                Venue  Venue Latitude  Venue Longitude  \
15                           Badmaash       34.051342      -118.244571   
160                          Badmaash       34.051342      -118.244571   
135                           Saffron       34.010517      -118.336472   
17                           Badmaash       34.051342      -118.244571   
55              India's Oven Westwood       34.048366      -118.435465   
62   Bhanu's Indian Grocery & Cuisine       34.128998      -118.072533   
58                    Flavor of India       34.097800      -118.363253   
67                           Badmaash       34.051342      -118.244571   
46                           Badmaash       34.051342      -118.244571   
122                          Badmaash       34.051342      -118.244571   
35                           Badmaash       34.051342      -118.244571   
89                           Badmaash       34.051342      -118.244571   
101                          Badmaash       34.051342      -118.244571   

        Venue Category  
15   Indian Restaurant  
160  Indian Restaurant  
135  Indian Restaurant  
17   Indian Restaurant  
55   Indian Restaurant  
62   Indian Restaurant  
58   Indian Restaurant  
67   Indian Restaurant  
46   Indian Restaurant  
122  Indian Restaurant  
35   Indian Restaurant  
89   Indian Restaurant  
101  Indian Restaurant

# Conclusion

**Most of the Indian restaurants are in cluster 2 which is around Green Field , Huntington Beach, Rocklin, Cupertino and Nevada City lowest in Cluster 1 areas which are in Auburn, Apple Valley, Adelanto and Barstow areas. Looking at nearby venues it seems cluster 0 might be a good location as it is a business area and there are not a lot of Indian restaurants in the areas like Redlands, Roseville, Seaside and Dana Point.**